**Purpose**

*   The code demonstrates blind source separation using ICA to recover the original signals (e.g., male and female voices) from their mixed version.
*   Practical applications include audio processing, speech separation, and noise removal.


    

# **Independent Component Analysis (ICA) using the FastICA**

This code demonstrates how to apply Independent Component Analysis (ICA) using the FastICA algorithm to separate mixed audio signals into their original independent sources. Here's a breakdown of the steps:

In [ ]:
from scipy.io import wavfile
import numpy as np
import pylab as pl
from sklearn.decomposition import PCA, FastICA
import IPython.display as ipd
import matplotlib.pyplot as plt
from sklearn.discriminant_analysis import StandardScaler
import os
import librosa

In [ ]:
from google.colab import drive
drive.mount('/gdrive')

Mounted at /gdrive


In [ ]:
os.chdir('/gdrive/My Drive/Audio_processing/23-02-2014')

In [ ]:
!ls -l

total 149507
-rw------- 1 root root  7696735 Jul  9 23:09  audio_process.ipynb
-rw------- 1 root root        0 Mar 15  2024  audio.rttm
-rw------- 1 root root 96701996 Feb 15  2024  Bdb001.interaction.wav
-rw------- 1 root root 13500113 Mar  5  2024  bdb001.wav
-rw------- 1 root root    58140 Apr  1  2024 'Copy of Untitled2.ipynb'
-rw------- 1 root root  5381824 Nov 16 16:50  Fastica.ipynb
-rw------- 1 root root   857260 Mar  2  2024  female.wav
-rw------- 1 root root      678 Mar  7  2024  locuteur_1.wav
-rw------- 1 root root      678 Mar  7  2024  locuteur_2.wav
-rw------- 1 root root   772012 Mar  2  2024  male.wav
-rw------- 1 root root  1543912 Mar  6  2024  mixing.wav
-rw------- 1 root root 10132880 Feb 10  2024  noise.wav
-rw------- 1 root root  1782411 Apr  1  2024  seaker_diarizition.ipynb
-rw------- 1 root root   771978 Mar  5  2024  Seperated11.wav
-rw------- 1 root root   771978 Mar  5  2024  Seperated22.wav
-rw------- 1 root root   771978 Mar  5  2024  source11.wav
-rw---

# *1. Load Audio Files*

In [ ]:
male_file = "male.wav"
ipd.Audio(male_file, rate=44100)

In [ ]:
female_file = "female.wav"
ipd.Audio(female_file, rate=44100)

In [ ]:
fs_1, male= wavfile.read(male_file)
fs_2, female = wavfile.read(female_file)
# Assurez-vous que les deux signaux audio ont la même longueur
m = min(len(male), len(female))
female = female[:m]
male = male[:m]

# *2. Create Source Matrix, beside Define and Generate Mixed Signals*

In [ ]:
# Empiler les signaux audio pour former la matrice de mélange
S = np.c_[male,female]
# Définir la matrice de mélange (hypothétique)
A = np.array([[1,1],[0.5,2]])
# Calculer les signaux observés (mélangés)
X = np.dot(S, A.T)
print(S)

[[  -1    0]
 [   0    0]
 [   1    0]
 ...
 [   6 1219]
 [   6 1976]
 [   6 2489]]


# *3.Normalize the Data*

In [ ]:
scaler = StandardScaler()
X_normalized = scaler.fit_transform(X)


In [ ]:
ipd.Audio("mixing.wav")

# *4. Apply ICA*

In [ ]:
# Appliquer FastICA
ica = FastICA(tol=0.01)
S_ = ica.fit(X_normalized).transform(X_normalized)
A_ = ica.mixing_
np.allclose(X, np.dot(S_, A_.T))

/usr/local/lib/python3.10/dist-packages/sklearn/decomposition/_fastica.py:542: FutureWarning: Starting in v1.3, whiten='unit-variance' will be used by default.
  warnings.warn(


False

# *5. Verify Reconstruction*

In [ ]:
# Vérifier la reconstruction
reconstructed_X = np.dot(S_, A_.T)
is_close = np.allclose(X_normalized, reconstructed_X)
print(is_close)

True


# *6. Rescale Separated Signals*

In [ ]:
multiply_factor = 1000000;

teamp_output_1 = multiply_factor*S_[:,0]
teamp_output_2 = multiply_factor*S_[:,1]

#wavfile.write("source11.wav", fs_2, teamp_output_1.astype(np.int16))
#wavfile.write("source22.wav", fs_2, teamp_output_2.astype(np.int16))

In [ ]:
ipd.Audio("source11.wav")

In [ ]:
ipd.Audio("source22.wav")

# *7. Plotting Observations, True Sources, and Recovered Signals*

After separating signals using FastICA, the following visualization code generates a side-by-side comparison of:

*   The observed mixed signals (X)
*   The original (true) sources (S)
*   The ICA-recovered signals (S_)



    
    
    

In [ ]:
import matplotlib.pyplot as plt

plt.figure()

models = [X, S, S_]
names = [
    "Observations (mixed signal)",
    "True Sources",
    "ICA recovered signals",
]
colors = ["red", "steelblue"]

for ii, (model, name) in enumerate(zip(models, names), 1):
    plt.subplot(3, 1, ii)
    plt.title(name)
    for sig, color in zip(model.T, colors):
        plt.plot(sig, color=color)

plt.tight_layout()
plt.show()

1.   **Top Plot**: Mixed signals (X) showing overlapping patterns from the two sources.
2.   **Middle Plot**: True source signals (S) used to create the mixture.
3.   **Bottom Plot**: Signals recovered by ICA (S_), ideally matching the true sources (S).



In [ ]:
!pip install SpeechRecognition
!pip install pydub

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.8/32.8 MB 35.8 MB/s eta 0:00:00


In [ ]:
import speech_recognition as sr
from pydub import AudioSegment

# Function to convert audio file to text
def transcribe_audio(audio_file_path, language='en-US'):
    # Load audio file
    audio_file = AudioSegment.from_file(audio_file_path)

    # Export audio file to wav format
    audio_file.export("temp.wav", format="wav")

    # Initialize recognizer class (for recognizing the speech)
    r = sr.Recognizer()

    # Open the audio file with read permission
    with sr.AudioFile("temp.wav") as source:
        # Using the audio file, we can extract audio data
        audio_data = r.record(source)

        # Recognize the speech using Google Speech Recognition
        try:
            text = r.recognize_google(audio_data, language=language)
            return text
        except Exception as e:
            print("Exception occurred: ", e)
            return None

# Reconnaître la parole dans chaque signal audio
text_1 = transcribe_audio("source11.wav")
text_2 = transcribe_audio("source22.wav")

# Afficher les résultats
print("Locuteur 1:", text_1)
print("Locuteur 2:", text_2)


Locuteur 1: hard work is the Cornerstone of success in any Endeavor it is the Relentless effort and dedication that Propel individuals towards their goals
Locuteur 2: hard work is the Cornerstone of success in any Endeavor it is the Relentless effort and dedication that Propel individuals towards their goals and aspirations
